In [1]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [2]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [3]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/PhysicalProgressReport/YearWiseHouseCompletionReport.aspx?"
params = {
    'params': 0
}
for key, value in params.items():
    url = url + "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [4]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddlFinYear'
scheme_select_name = 'ctl00$ContentPlaceHolder1$ddlScheme'
state_select_name = 'ctl00$ContentPlaceHolder1$ddlState'
district_select_name = 'ctl00$ContentPlaceHolder1$ddlDistrict'
block_select_name = 'ctl00$ContentPlaceHolder1$ddlBlock'
submit_button_name = 'ctl00$ContentPlaceHolder1$btnSubmit'
content_table_pane = 'ContentPlaceHolder1_gvDataPanelItem'
content_table_head_id = 'ContentPlaceHolder1_gvDataCopy'
content_table_id = 'ContentPlaceHolder1_gvData'

In [5]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

#Check Submit button
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )

#Check table
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )    
    
#Check submit button
def delete_content():
    driver.execute_script("return document.getElementsByClassName('col-lg-10')[0].remove()")
def check_error():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.ID, "ContentPlaceHolder1_lbl_data_msg" ) ) )
    

In [6]:
def get_total_houselist():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
    WebDriverWait(driver, 2).until(element_present)
    #Once Loaded Create DataFrame from Table
    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
    df = pd.read_html(html_table, skiprows=0, header=0)[0]
    df = df[1:-1]        
    total_houses_completed = list(df[df.columns[-1]])
    return total_houses_completed

In [7]:
#Start Chrome
driver.get(url)

#Year Selection
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[2:3]
for year in yearlist:    
    print("--Scrapping data for Year: ", year['text'])
    year_query = ".//option[@value='" + year['value'] + "']"
    delete_submit()
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    check_submit()
    
    #DataStore
    df_list = []
    
    #Scheme Selection
    schemelist = build_list(scheme_select_name)[1:]
    for scheme in schemelist:
        print("--//--Scrapping data for scheme: ", scheme['text'])
        scheme_query = ".//option[@value='" + scheme['value'] + "']"
        delete_submit()
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, scheme_select_name))
        )
        element.find_element_by_xpath(scheme_query).click()
        check_submit()
        
        # Delete Content
        delete_content()        
        #Submit button
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, submit_button_name))
        )
        element.click()
        
        #Load Filter List
        state_total_houses_completed = get_total_houselist();
        
        #state Selection
        statelist = build_list(state_select_name)
        for stateindex, state in enumerate(statelist):
            print("--//--//--Scrapping data for state: ", state['text'])
            if state_total_houses_completed[int(stateindex)] > 0:
                print(stateindex)
                state_query = ".//option[@value='" + state['value'] + "']"
                delete_submit()
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, state_select_name))
                )
                element.find_element_by_xpath(state_query).click()
                check_submit()
                
                # Delete Content
                delete_content()        
                #Submit button
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                )
                element.click()

                #Load Filter List
                district_total_houses_completed = get_total_houselist();
         
                #district Selection
                districtlist = build_list(district_select_name)
                for districtindex, district in enumerate(districtlist):
                    print("--//--//--//--Scrapping data for district: ", district['text'])
                    if district_total_houses_completed[int(districtindex)] > 0:
                        district_query = ".//option[@value='" + district['value'] + "']"
                        delete_submit()
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, district_select_name))
                        )
                        element.find_element_by_xpath(district_query).click()
                        check_submit()
                        
                        # Delete Content
                        delete_content()        
                        #Submit button
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, submit_button_name))
                        )
                        element.click()

                        #Load Filter List
                        block_total_houses_completed = get_total_houselist();

                        #block Selection
                        blocklist = build_list(block_select_name)
                        for blockindex, block in enumerate(blocklist):
                            print("--//--//--//--//--Scrapping data for block: ", block['text'])
                            if block_total_houses_completed[int(blockindex)] > 0:
                                block_query = ".//option[@value='" + block['value'] + "']"
                                delete_submit()
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, block_select_name))
                                )
                                element.find_element_by_xpath(block_query).click()
                                check_submit()

                                # Delete Content
                                delete_content()

                                #Submit button
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                                )
                                element.click()

                                try:
                                    #Wait for Table to Load fully
                                    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
                                    WebDriverWait(driver, 2).until(element_present)

                                    #Once Loaded Create DataFrame from Table
                                    #html_head = driver.find_element_by_id(content_table_head_id).get_attribute('outerHTML')
                                    #df = pd.read_html(html_head, skiprows=0)[0]
                                    #table_head = list(df.values[0])
                                    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
                                    df = pd.read_html(html_table, skiprows=0, header=0)[0]
                                    df = df[1:-1]
                                    #df.columns = table_head
                                    df['Financial Year'] = year['text']
                                    df['Scheme'] = scheme['text']
                                    df['State Name'] = state['text']
                                    df['District Name'] = district['text']
                                    df['Block Name'] = block['text']
                                    df_list.append(df)
                                except Exception as e:
                                    print("Error while table data |", e)


    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df = df.reset_index().drop(columns=['index', '#SNo'])
    df['#SNo'] = df.index + 1
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

--Scrapping data for Year:  2012-2013
--//--Scrapping data for scheme:  ALL CENTRAL SCHEMES
--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
1
--//--//--//--Scrapping data for district:  BAKSA
--//--//--//--//--Scrapping data for block:  BARAMA
--//--//--//--//--Scrapping data for block:  BASKA
--//--//--//--//--Scrapping data for block:  DHAMDHAMA
--//--//--//--//--Scrapping data for block:  GOBARDHANA(BTC)
--//--//--//--//--Scrapping data for block:  GORESWAR
--//--//--//--//--Scrapping data for block:  JALAH(BTC)
--//--//--//--//--Scrapping data for block:  NAGRIJULI
--//--//--//--//--Scrapping data for block:  TAMULPUR
--//--//--//--Scrapping data for district:  BARPETA
--//--//--//--//--Scrapping data for block:  BAJALI
--//--//--//--//--Scrapping data for block:  BARPETA
--//--//--//--//--Scrapping data for block:  BHAWANIPUR
--//--//--//--//--Scrapping data for block:  CHAKCHAKA
--//--//--//--//--Scrapping data for block:  CHENGA


--//--//--//--//--Scrapping data for block:  BADARPUR
--//--//--//--//--Scrapping data for block:  DULLAVCHERRA
--//--//--//--//--Scrapping data for block:  LOWAIRPOA
--//--//--//--//--Scrapping data for block:  NORTH KARIMGJANJ
--//--//--//--//--Scrapping data for block:  PATHARKANDI
--//--//--//--//--Scrapping data for block:  RAMKRISHNA NAGAR
--//--//--//--//--Scrapping data for block:  SOUTH KARIMGANJ
--//--//--//--Scrapping data for district:  KOKRAJHAR
--//--//--//--//--Scrapping data for block:  BILASHIPARA-BTC
--//--//--//--//--Scrapping data for block:  CHAPOR-SALKOCHA-BTC
--//--//--//--//--Scrapping data for block:  DEBITOLA-BTC
--//--//--//--//--Scrapping data for block:  DOTOMA
--//--//--//--//--Scrapping data for block:  GOLAKGANJ-BTC
--//--//--//--//--Scrapping data for block:  GOSSAIGAON
--//--//--//--//--Scrapping data for block:  HATIDHURA
--//--//--//--//--Scrapping data for block:  KACHUGAON
--//--//--//--//--Scrapping data for block:  KOKRAJHAR
--//--//--//--//--Scr

--//--//--//--//--Scrapping data for block:  DHURAIYA
--//--//--//--//--Scrapping data for block:  FULLIDUMAR
--//--//--//--//--Scrapping data for block:  KATORIA
--//--//--//--//--Scrapping data for block:  RAJAUN
--//--//--//--//--Scrapping data for block:  SHAMBHUGANJ
--//--//--//--Scrapping data for district:  BEGUSARAI
--//--//--//--//--Scrapping data for block:  BACHHWARA
--//--//--//--//--Scrapping data for block:  BAKHRI
--//--//--//--//--Scrapping data for block:  BALIA
--//--//--//--//--Scrapping data for block:  BARAUNI
--//--//--//--//--Scrapping data for block:  BEGUSARAI
--//--//--//--//--Scrapping data for block:  BHGWANPUR
--//--//--//--//--Scrapping data for block:  BIRPUR
--//--//--//--//--Scrapping data for block:  CHERIA BARIARPUR
--//--//--//--//--Scrapping data for block:  CHHAURAHI
--//--//--//--//--Scrapping data for block:  DANDARI
--//--//--//--//--Scrapping data for block:  GARHPURA
--//--//--//--//--Scrapping data for block:  KODABANPUR
--//--//--//--//--Scr

--//--//--//--//--Scrapping data for block:  DURGAWATI
--//--//--//--//--Scrapping data for block:  KUDRA
--//--//--//--//--Scrapping data for block:  MOHANIA
--//--//--//--//--Scrapping data for block:  NUAON
--//--//--//--//--Scrapping data for block:  RAMGARH
--//--//--//--//--Scrapping data for block:  RAMPUR
--//--//--//--Scrapping data for district:  KATIHAR
--//--//--//--//--Scrapping data for block:  AMDABAD
--//--//--//--//--Scrapping data for block:  AZAMNAGAR
--//--//--//--//--Scrapping data for block:  BALRAMPUR
--//--//--//--//--Scrapping data for block:  BARARI
--//--//--//--//--Scrapping data for block:  BARSOI
--//--//--//--//--Scrapping data for block:  DANDKHORA
--//--//--//--//--Scrapping data for block:  FALKA
--//--//--//--//--Scrapping data for block:  HASANGANJ
--//--//--//--//--Scrapping data for block:  KADWA
--//--//--//--//--Scrapping data for block:  KATIHAR
--//--//--//--//--Scrapping data for block:  KORHA
--//--//--//--//--Scrapping data for block:  KURSE

--//--//--//--//--Scrapping data for block:  CHANPATIA
--//--//--//--//--Scrapping data for block:  GAUNAHA
--//--//--//--//--Scrapping data for block:  JOGAPATTI
--//--//--//--//--Scrapping data for block:  LAURIYA
--//--//--//--//--Scrapping data for block:  MADHUBANI
--//--//--//--//--Scrapping data for block:  MAINATAND
--//--//--//--//--Scrapping data for block:  MAJHAULIA
--//--//--//--//--Scrapping data for block:  NARKATIAGANJ
--//--//--//--//--Scrapping data for block:  NAUTAN
--//--//--//--//--Scrapping data for block:  PIPRASI
--//--//--//--//--Scrapping data for block:  RAMNAGAR
--//--//--//--//--Scrapping data for block:  SIKTA
--//--//--//--//--Scrapping data for block:  THAKRAHAN
--//--//--//--Scrapping data for district:  PATNA
--//--//--//--//--Scrapping data for block:  ATHMALGOLA
--//--//--//--//--Scrapping data for block:  BAKHTIYARPUR
--//--//--//--//--Scrapping data for block:  BARH
--//--//--//--//--Scrapping data for block:  BELCHHI
--//--//--//--//--Scrapping d

...

--//--//--//--//--Scrapping data for block:  MOHAMMADI
--//--//--//--//--Scrapping data for block:  NAKAHA
--//--//--//--//--Scrapping data for block:  NIGHASAN
--//--//--//--//--Scrapping data for block:  PALIA
--//--//--//--//--Scrapping data for block:  PASGAWAN
--//--//--//--//--Scrapping data for block:  PHOOLBEHAR
--//--//--//--//--Scrapping data for block:  RAMIA BEHAR
--//--//--//--Scrapping data for district:  KUSHI NAGAR
--//--//--//--Scrapping data for district:  LALITPUR
--//--//--//--Scrapping data for district:  LUCKNOW
--//--//--//--Scrapping data for district:  MAHAMAYA NAGAR
--//--//--//--Scrapping data for district:  MAHARAJGANJ
--//--//--//--Scrapping data for district:  MAHOBA
--//--//--//--Scrapping data for district:  MAINPURI
--//--//--//--Scrapping data for district:  MATHURA
--//--//--//--Scrapping data for district:  MAU
--//--//--//--Scrapping data for district:  MEERUT
--//--//--//--Scrapping data for district:  MIRZAPUR
--//--//--//--Scrapping data for dist

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
5
--//--//--//--Scrapping data for district:  AHMADABAD
--//--//--//--Scrapping data for district:  AMRELI
--//--//--//--Scrapping data for district:  ANAND
--//--//--//--Scrapping data for district:  ARVALLI
--//--//--//--Scrapping data for district:  BANAS KANTHA
--//--//--//--Scrapping data for district:  BHARUCH
--//--//--//--Scrapping data for district:  BHAVNAGAR
--//--//--//--Scrapping data for district:  BOTAD
--//--//--//--Scrapping data for district:  CHHOTAUDEPUR
--//--//--//--Scrapping data for district:  DANG
--//--//--//--Scrapping data for district:  DEVBHUMI DWARKA
--//--//--//--Scrapping data for district:  DOHAD
--//--//--//--Scrapping data for district:  GANDHINAGAR
--//--//--//--Scrapping data 

--//--//--//--Scrapping data for district:  GUMLA
--//--//--//--Scrapping data for district:  HAZARIBAGH
--//--//--//--Scrapping data for district:  JAMTARA
--//--//--//--Scrapping data for district:  KHUNTI
--//--//--//--Scrapping data for district:  KODERMA
--//--//--//--Scrapping data for district:  LATEHAR
--//--//--//--Scrapping data for district:  LOHARDAGA
--//--//--//--Scrapping data for district:  PAKUR
--//--//--//--Scrapping data for district:  PALAMU
--//--//--//--Scrapping data for district:  RAMGARH
--//--//--//--Scrapping data for district:  RANCHI
--//--//--//--Scrapping data for district:  SAHEBGANJ
--//--//--//--Scrapping data for district:  SARAIKELA KHARSAWAN
--//--//--//--Scrapping data for district:  SIMDEGA
--//--//--//--Scrapping data for district:  WEST SINGHBHUM
--//--//--Scrapping data for state:  KERALA
10
--//--//--//--Scrapping data for district:  ALAPPUZHA
--//--//--//--//--Scrapping data for block:  AMBALAPUZHA
--//--//--//--//--Scrapping data for block:

--//--//--//--//--Scrapping data for block:  AMBERNATH
--//--//--//--//--Scrapping data for block:  BHIWANDI
--//--//--//--//--Scrapping data for block:  KALYAN
--//--//--//--//--Scrapping data for block:  MURBAD
--//--//--//--//--Scrapping data for block:  SHAHAPUR
--//--//--//--//--Scrapping data for block:  THANE
--//--//--//--//--Scrapping data for block:  ULHASNAGAR
--//--//--//--Scrapping data for district:  WARDHA
--//--//--//--Scrapping data for district:  WASHIM
--//--//--//--Scrapping data for district:  YAVATMAL
--//--//--Scrapping data for state:  MANIPUR
--//--//--Scrapping data for state:  MEGHALAYA
--//--//--Scrapping data for state:  MIZORAM
--//--//--Scrapping data for state:  NAGALAND
--//--//--Scrapping data for state:  ODISHA
--//--//--Scrapping data for state:  PUNJAB
--//--//--Scrapping data for state:  RAJASTHAN
--//--//--Scrapping data for state:  SIKKIM
--//--//--Scrapping data for state:  TAMIL NADU
--//--//--Scrapping data for state:  TRIPURA
22
--//--//--//-

--//--//--//--//--Scrapping data for block:  ASPUR DEOSARA
--//--//--//--//--Scrapping data for block:  BABA BELKHARNATH DHAM
--//--//--//--//--Scrapping data for block:  BABAGANJ
--//--//--//--//--Scrapping data for block:  BIHAR
--//--//--//--//--Scrapping data for block:  GAURA
--//--//--//--//--Scrapping data for block:  KALAKANKAR
--//--//--//--//--Scrapping data for block:  KUNDA
--//--//--//--//--Scrapping data for block:  LAKSHAMANPUR
--//--//--//--//--Scrapping data for block:  LALGANJ
--//--//--//--//--Scrapping data for block:  MAGRAURA
--//--//--//--//--Scrapping data for block:  MANDHATA
--//--//--//--//--Scrapping data for block:  PATTI
--//--//--//--//--Scrapping data for block:  PRATAPGARH (SADAR)
--//--//--//--//--Scrapping data for block:  RAMPUR SANRAMGARH
--//--//--//--//--Scrapping data for block:  SANDWA CHANDRIKA
--//--//--//--//--Scrapping data for block:  SANGIPUR
--//--//--//--//--Scrapping data for block:  SHIVGARH
--//--//--//--Scrapping data for district:  

In [ ]:
df = pd.concat(df_list)

In [46]:
df

#SNo                    Panchayat Name  \
1    1.0            Araria Basti Panchayat   
2    2.0                 Bangama Panchayat   
3    3.0                Bansbari Panchayat   
4    4.0               Basantpur Panchayat   
5    5.0               Baturbari Panchayat   
6    6.0                   Belwa Panchayat   
7    7.0                   Bochi Panchayat   
8    8.0              Chandardei Panchayat   
9    9.0                  Chatar Panchayat   
10  10.0                  Chikni Panchayat   
11  11.0                  Diyari Panchayat   
12  12.0                   Gaira Panchayat   
13  13.0                 Gaiyari Panchayat   
14  14.0                  Hariya Panchayat   
15  15.0                Hayatpur Panchayat   
16  16.0                   Jamua Panchayat   
17  17.0                  Jhamta Panchayat   
18  18.0               Kamaldaha Panchayat   
19  19.0        Kismat Khawaspur Panchayat   
20  20.0             Kusiyargaon Panchayat   
21  21.0            Madanpur (E) Panchayat   
22  22.0            Madanpur (W) Panchayat   
23  23.0                Paiktola Panchayat   
24  24.0               Pakhariya Panchayat   
25  25.0       Rampur Kodarkatti Panchayat   
26  26.0     Rampur Mohanpur (E) Panchayat   
27  27.0     Rampur Mohanpur (W) Panchayat   
28  28.0                Sahasmal Panchayat   
29  29.0               Sharanpur Panchayat   
30  30.0         Tatouna Bhojpur Panchayat   
..   ...                               ...   
13  13.0                             KURMA   
14  14.0                             LAGMA   
15  15.0                       MAISHAMUNDA   
16  16.0                        MATHURAPUR   
17  17.0                  MOHANPUR GOGATTA   
18  18.0                        NANDLALPUR   
19  19.0                             OGREE   
20  20.0                             ORIAP   
21  21.0                        PAKKISARAI   
22  22.0  PARASHATHDIH (SHANKARPUR KHAWAS)   
23  23.0                        RAMJANIPUR   
24  24.0                            RAMPUR   
25  25.0                 SADANANDPUR BAISA   
26  26.0                    SALEMPUR SAINI   
27  27.0                          SHYAMPUR   
28  28.0                              SIYA   
1    1.0                 ABHIA PACHGACHHIA   
2    2.0               BABU TOLA KAMLAKUND   
3    3.0                DUMARIA CHAPARGHAT   
4    4.0                   GOPALPUR DIMAHA   
5    5.0                       GOSAI GAOWN   
6    6.0                         MAKANDPUR   
7    7.0                           SAIDPUR   
8    8.0                     SUKATIA BAZAR   
9    9.0                   TINTANGA KARARI   
1    1.0            ISHMAILPUR EAST BHITHA   
2    2.0            ISHMAILPUR WEST BHITHA   
3    3.0                         KAMLAKUND   
4    4.0                NARAINPUR LAXMIPUR   
5    5.0                          PARVATTA   

    Houses completed for prior to 2005-2006  Houses completed for 2006-2007  \
1                                         0                               0   
2                                         0                               0   
3                                         0                               0   
4                                         0                               0   
5                                         0                               0   
6                                         0                               0   
7                                         0                               0   
8                                         0                               0   
9                                         0                               0   
10                                        0                               0   
11                                        0                               0   
12                                        0                               0   
13                                        0                               0   
14                                        0  

In [12]:
#merge all dataframes to master dataframe
df = pd.concat(df_list)
df = df.reset_index().drop(columns=['index', '#SNo'])
df['#SNo'] = df.index + 1
#Save Scrapped File
df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)